In [1]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import seaborn as sns
import patsy
import imp
import os
import pymc3 as pm

plt.style.use('fivethirtyeight')

from sklearn import grid_search, datasets
from sklearn.neighbors import KNeighborsClassifier, KNeighborsRegressor
from sklearn.cross_validation import cross_val_score, cross_val_predict, train_test_split, StratifiedKFold
from sklearn.grid_search import GridSearchCV, RandomizedSearchCV
from sklearn.linear_model import LinearRegression as lm, LogisticRegression as lr, Lasso, Ridge, ElasticNet, LassoCV, RidgeCV, ElasticNetCV
from sklearn.preprocessing import StandardScaler, LabelEncoder
from ipywidgets import *
from IPython.display import display
from collections import defaultdict
from sklearn.linear_model import LogisticRegression
from sklearn.cross_validation import train_test_split

%matplotlib inline
%config InlineBackend.figure_format = 'retina'


WARNING (theano.configdefaults): Only clang++ is supported. With g++, we end up with strange g++/OSX bugs.


Couldn't import dot_parser, loading of dot files will not be possible.


In [2]:
# All .xls files from C_comp_EC_MAR31

EC = defaultdict()
sheets = ['Perc', 'Mean_C_PROB', 'Mean_C_MATH', 'Mean_C_READ']
keys = []

base_dir = "/Users/nichollejames/Desktop/capstone_project/assets/compressed_compendium_files/C_comp_EC_MAR31/"
for f in os.listdir(base_dir): 
    if f.endswith(".xls"):
        key = f.split('.')[0]
        keys.append(key)
        
        for sheet in sheets:
            
            if key not in EC:
                EC[key] = {}
            
            EC[key].update({
                sheet:  pd.read_excel(base_dir+f, sheetname=sheet, skiprows = 1)       
            })

# EC[x][y] change all of the column names

for x in EC:
    for y in sheets:
        EC[x][y] = EC[x][y].rename(columns={' ': 'cnt',
                                            'N': 'total_number_of_resp',
                                            'N/A': 'pct_not_valid',
                                            'N.1': 'no_of_valid_resp',
                                            'No, never': 'resp_no_never_pct',
                                            'No, never.1': 'resp_no_never_se',
                                            'No, never  .1': 'resp_no_never_se',
                                            'No, never  ': 'res_no_never_mean',
                                            'Yes, once' : 'resp_yes_once_pct',
                                            'Yes, once  .1': 'resp_yes_once_se',
                                            'Yes, once  ': 'resp_yes_once_mean',
                                            'Yes, twice or more': 'resp_yes_twice_or_more_pct',
                                            'Yes, twice or more  .1': 'resp_yes_twice_or_more_se',
                                            'Yes, twice or more  ': 'resp_yes_twice_or_more_mean',
                                            'Mostly <heritage language> ': 'resp_mostly_heritage_language_pct',
                                            'Mostly <heritage language> .1': 'resp_mostly_heritage_languagee_se',
                                            'About equally <heritage language> and <test language>': 'resp_about_equally_heritage_language_and_test_language_pct',
                                            'About equally <heritage language> and <test language>.1': 'resp_about_equally_heritage_language_and_test_language_se',
                                            'Mostly <test language>': 'resp_mostly_test_language_pct',
                                            'Mostly <test language>.1': 'resp_mostly_test_language_se',
                                            'Not applicable': 'resp_not_applicable_pct',
                                            'Not applicable.1': 'resp_not_applicable_se',
                                            'Tick': 'resp_tick_pct',
                                            'Tick.1': 'resp_tick_se',
                                            'No tick': 'resp_no_tick_pct',
                                            'No tick.1': 'resp_no_tick_se',
                                            'Strongly agree': 'resp_strongly_agree_pct',
                                            'Strongly agree.1': 'resp_strongly_agree_se',
                                            'Agree': 'resp_agree_pct',
                                            'Agree.1': 'resp_agree_se',
                                            'Disagree': 'resp_disagree_pct',
                                            'Disagree.1': 'resp_disagree_se',
                                            'Strongly disagree': 'resp_strongly_disagree_pct',
                                            'Strongly disagree.1': 'resp_strongly_disagree_se',
                                            'No': 'resp_no_pct',
                                            'No.1': 'resp_no_se',
                                            'Yes': 'resp_yes_pct',
                                            'Yes.1': 'resp_yes_se',
                                            '0 to 3 years': 'resp_0_to_3_years_pct',
                                            '0 to 3 years.1': 'resp_0_to_3_years_se',
                                            '4 to 6 years': 'resp_4_to_6_years_pct',
                                            '4 to 6 years.1': 'resp_4_to_6_years_se',
                                            '7 to 9 years': 'resp_7_to_9_years_pct',
                                            '7 to 9 years.1': 'resp_7_to_9_years_se',
                                            '10 to 12 years': 'resp_10_to_12_years_pct',
                                            '10 to 12 years.1': 'resp_10_to_12_years_se',
                                            '13 years or older': 'resp_13_years_or_older_pct',
                                            '13 years or older.1': 'resp_13_years_or_older_se',
                                            
                                            '<test language> or <other official national languages or dialects> ': 'resp_test_language_or_other_official_national_languages_or_dialects_pct',
                                            '<test language> or <other official national languages or dialects> .1': 'resp_test_language_or_other_official_national_languages_or_dialects_se',
                                            '<test language> or <other official national languages or dialects> and another language': 'resp_test_language_or_other_official_national_languages_or_dialects_and_another_language_pct',
                                            '<test language> or <other official national languages or dialects> and another language.1': 'resp_test_language_or_other_official_national_languages_or_dialects_and_another_language_se',
                                            'other than <test language> and <other official national languages or dialects> ': 'resp_other_than_test language_and_other_official_national_languages_or_dialects_pct',
                                            'other than <test language> and <other official national languages or dialects> .1': 'resp_other_than_test language_and_other_official_national_languages_or_dialects_se',
#                                             '13 years or older': 'resp_13_years_or_older_pct',
#                                             '13 years or older.1': 'resp_13_years_or_older_se',
#                                             '13 years or older': 'resp_13_years_or_older_pct',
#                                             '13 years or older.1': 'resp_13_years_or_older_se',
#                                             '13 years or older': 'resp_13_years_or_older_pct',
#                                             '13 years or older.1': 'resp_13_years_or_older_se',
#                                             '13 years or older': 'resp_13_years_or_older_pct',
#                                             '13 years or older.1': 'resp_13_years_or_older_se',
                                            
                                            'Missing': 'resp_missing_mean',
                                            'Missing.1': 'resp_missing_se',
                     })
        
# Delete the first row since it was inserted into the column headers
for x in EC:
    for y in sheets:
        EC[x][y] = EC[x][y][EC[x][y].resp_missing_mean != 'Mean']     
        
        EC[x][y].columns = [col.replace('(', '').replace(')','') for col in EC[x][y].columns]

            
            
# Run this only once or the column names will have the keys repeated.

# lvl1keys = EC.keys()

# for l1key in lvl1keys:
#     lvl2keys = EC[l1key].keys()
# #     print lvl2keys
#     for l2key in lvl2keys:
#         current_columns = EC[l1key][l2key].columns
#         EC[l1key][l2key].columns = [l1key+'_'+l2key+'_'+x if x!='cnt' else x for x in current_columns]
        

# # Merge all the dataframes together

# df_EC = pd.DataFrame(EC['EC01Q01']['Perc'])

# for filename, worksheets in EC.items():
#     print "Merging: ", filename

#     for worksheet, sheet_df in worksheets.items():
#         # print worksheet, sheet_df.columns
#         df_EC = pd.merge(df_EC, sheet_df, how="inner", on="cnt")



In [42]:
# iowa['zip_code'].replace(51529,'51529',inplace=True)

In [43]:
# for x in EC:
#     for y in sheets:
# = p.replace('(', '').replace(')','')

IndentationError: expected an indented block (<ipython-input-43-51a3a05fdf27>, line 3)

In [ ]:
#EC['EC04Q03B']['Mean_C_MATH'].replace('(','', inplace = True)


def paren_cleaner(x,y):
    for x in EC:
        for y in sheets:
            columns = [EC[x][y].columns.tolist()]
            for col in columns:
                print EC[x][y][col]
                EC[x][y][col] = EC[x][y][col].replace('(', '').replace(')','')
                print EC[x][y][col]

                #                 for p in col:
#                     p = p.replace('(', '').replace(')','')


paren_cleaner(x,y)

                         cnt total_number_of_resp pct_not_valid  \
0                        NaN                  ALL             %   
1                  Australia               250711           100   
2                    Austria                82225       2.05505   
3                    Belgium               117889       3.90119   
4                     Canada               347987       1.38883   
5                      Chile               229159           100   
6             Czech Republic              82250.1           100   
7                    Denmark                65642       2.79744   
8                    Estonia              11626.5           100   
9                    Finland              60047.2       1.75456   
10                    France               699779           100   
11                   Germany               756907       16.0501   
12                   Hungary              91178.6           100   
13                   Ireland              54010.3      0.46639

In [50]:
EC['EC04Q03B']['Mean_C_MATH'].resp_tick_se.values

array([u'(1.92)', u'(4.17)', u'(3.33)', u'(2.19)', u' ', u' ', u'(4.21)',
       u' ', u' ', u' ', u' ', u'(4.35)', u'(4.12)', u' ', u'(4.58)', u' ',
       u'(5.90)', u' ', u' ', u' ', u'(3.85)', u'(3.35)', u'(2.84)', u' ',
       u' ', u' ', u' ', u' ', u'(1.03)', u'(1.83)', u' ', u' ', u'(4.80)',
       u' ', u' ', u' ', u' ', u'(4.83)', u'(2.14)', u' ', u' ', u' ',
       u' ', u'(3.01)', u' ', u' '], dtype=object)

In [33]:
EC['EC04Q03B']['Mean_C_MATH'].head()

cnt total_number_of_resp pct_not_valid no_of_valid_resp  \
1  Australia               250711       1.17875           247756   
2    Austria                82225       2.05505          80535.3   
3    Belgium               117889       3.90119           113290   
4     Canada               347987       1.38883           343154   
5      Chile               229159           100                0   

  resp_tick_pct resp_tick_se resp_no_tick_pct resp_no_tick_se  \
1       507.802       (1.92)          508.107          (1.98)   
2       497.447       (4.17)          513.138          (3.56)   
3       509.426       (3.33)          521.156          (2.57)   
4       523.382       (2.19)          523.057          (2.72)   
5                                                               

  resp_missing_mean resp_missing_se  
1            485.13          (6.67)  
2                                    
3                                    
4            510.41         (23.04)  
5